# Fogo Cruzado: Incidência de Crimes e Tiroteios

# Parâmetros

In [62]:
ibge_ids = [3303302, 3304904, 3301900]
ibge_ids = [3304557]

In [52]:
from getpass import getpass
from itertools import product
import pathlib
import re
import warnings

import contextily as cx
from crossfire import Client
import geobr
import geopandas as gpd
import ipeadatapy
import libpysal.weights as pysal
import matplotlib.pyplot as plt
import numpy as np
import osmnx as ox
import pandas as pd
import pandana as pdna
import partridge as ptg
from scipy.stats import zscore
from sklearn.neighbors import KernelDensity
from shapely.geometry import LineString, Point
from shapely.ops import split
import seaborn as sns
from libpysal.io.fileio import FileIO
from tobler.area_weighted import area_interpolate
from tobler.util import h3fy

# Study Area

In [63]:
def filter_by_code_muni(code_muni):
    """
    Return metro areas filtered by municipality code(s), optionally projected.

    Parameters
    ----------
    code_muni : int, str, or iterable of int/str
        Municipality code(s) to filter.
    out_crs : int or str, optional
        Output CRS for projection.

    Returns
    -------
    geopandas.GeoDataFrame
        Filtered and (optionally) projected metro areas.
    """
    metro = geobr.read_metro_area()
    metro['code_muni'] = metro['code_muni'].astype(int)
    out_crs = metro.estimate_utm_crs(datum_name='SIRGAS 2000')

    # Normalize input to a list of ints
    if isinstance(code_muni, (int, str)):
        codes = [int(code_muni)]
    elif hasattr(code_muni, '__iter__'):
        codes = [
            int(x) for x in code_muni
            if isinstance(x, (int, str)) and str(x).isdigit()
        ]
        if not codes:
            raise ValueError("No valid municipality codes found in input.")
    else:
        raise ValueError(
            "code_muni must be int, str of digits, or iterable of those."
        )

    filtered = metro[metro['code_muni'].isin(codes)]

    if out_crs is not None:
        filtered = filtered.to_crs(out_crs)

    return filtered

In [64]:
area = filter_by_code_muni(ibge_ids)

## Segurança Pública

In [65]:
isp1 = pd.read_csv(
    '../database/6. Segurança Pública/Pedido_081_2023_part_1.csv',
    encoding='latin-1',
    sep=';',
    )
isp2 = pd.read_csv(
    '../database/6. Segurança Pública/Pedido_081_2023_part_2.csv',
    encoding='latin-1',
    sep=';',
    )

isp = pd.concat([isp1, isp2], ignore_index=True)

del isp1, isp2

In [66]:
isp = (
    isp
    .loc[
        (isp.local == 'Via pública')
        & (isp.titulo_do != 'Encontro de ossada')
        #& (isp.ano == 2019)
        & ~(isp.titulo_do.str.contains('estupr', case=False))
        ]
    .assign(
        shape_id=lambda x: x.cisp.str.extract(r'(\d{3}).*').astype(int),
        titulo_do=lambda x: np.where(
            x.titulo_do.str.contains('roubo|extors|morte|homic', case=False),
            'violent_crime',
            x.titulo_do,
            )
        )
    .assign(
        titulo_do=lambda x: np.where(
            x.titulo_do.str.contains('furto', case=False),
            'non_violent_crime',
            x.titulo_do,
            )
         )
    )

In [67]:
isp.head(3)

controle   ano      mes                   titulo          titulo_do  \
0  00132271-2018  2018  Janeiro             Furto outros  non_violent_crime   
2  00490161-2018  2018  Janeiro             Roubo outros      violent_crime   
3  00504871-2018  2018  Janeiro  Furto de Veículo - Moto  non_violent_crime   

  total_rbft  lei conteudo                         dp  \
0      Furto  Não    casos           012a. Copacabana   
2      Roubo  Não    casos               019a. Tijuca   
3      Furto  Não    casos  125a. São Pedro da Aldeia   

                        cisp  ...           sexo data_nasc idade  \
0            005a. Mem de Sá  ...  não se aplica       NaN   NaN   
2               019a. Tijuca  ...  não se aplica       NaN   NaN   
3  125a. São Pedro da Aldeia  ...  não se aplica       NaN   NaN   

             cor escolaridade      profissao        relacao     bairro_vit  \
0  não se aplica          NaN  não se aplica  Não se aplica  não se aplica   
2  não se aplica          NaN  não se aplica  Não se aplica  não se aplica   
3  não se aplica          NaN  não se aplica  Não se aplica  não se aplica   

   municipio_vit shape_id  
0  não se aplica        5  
2  não se aplica       19  
3  não se aplica      125  

[3 rows x 29 columns]

In [68]:
crime_to_plot = (
    isp
    .groupby(
        ['ano', 'mes', 'shape_id', 'titulo_do']
        )
    .size()
    .round()
    .unstack('titulo_do')
    .groupby(level='shape_id')
    .median()
    .astype(int)
    .rename_axis('crime_nature', axis='columns')
    )

In [69]:
crime_to_plot.head(3)

crime_nature  non_violent_crime  violent_crime
shape_id                                      
1                            62             77
4                            62             60
5                           106            113

In [70]:
cisp = gpd.read_file(
    '../database/6. Segurança Pública/CISPshp.zip'
    )

In [71]:
cisp = (
    cisp
    .to_crs(epsg=31983)
    .sjoin(
        area.buffer(-500).to_frame('study_area'),
    )
    .drop_duplicates(subset='dp')
    .merge(crime_to_plot, left_on='dp', right_index=True)
    )

In [72]:
cisp.explore('violent_crime', scheme='NaturalBreaks', cmap='RdYlBu_r')

c:\Users\brand\anaconda3\envs\roda\Lib\site-packages\sklearn\cluster\_kmeans.py:1419: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=1.
  warnings.warn(


## Fogo Cruzado

In [73]:
client = Client(
    email=getpass('e-mail: '),
    password=getpass('senha: ')
)

In [74]:
def get_city_ids(area, client):
    city_names = area.name_muni.str.upper()
    city_ids = client.cities(format='df')
    return city_ids[city_ids.name.isin(city_names)].id.tolist()


In [75]:
shots = client.occurrences(
    id_state='b112ffbe-17b3-4ad0-8f2a-2038745d1d14', #RJ
    id_cities=get_city_ids(area, client), # Rio de Janeiro
    type_occurrence='all',
    format='geodf'
    )

shots = (
    shots
    .reindex(
        columns=[
            'id',
            'date',
            'policeAction',
            'agentPresence',
            'relatedRecord',
            'contextInfo',
            'transports',
            'victims',
            'animalVictims',
            'geometry'
            ]
        )
    .assign(
        contextInfo=lambda x: x.contextInfo.map(
                                    lambda x: x.get('mainReason').get('name')
                                    )
        )
    .to_crs(31983)
    )

shots.head()

Loading pages: 100%|██████████| 539/539 [10:12<00:00,  1.14s/page] 


id                      date  \
0  bff14f2b-f468-46d9-a82d-3ea2cb8e0011  2016-07-05T00:00:00.000Z   
1  66003d3f-d859-40d7-826a-97210c501ff8  2016-07-05T00:00:00.000Z   
2  3b23c7f6-5604-4bff-a8eb-d0ab31121ba0  2016-07-05T00:40:00.000Z   
3  dddc418e-222b-4be1-9d2a-b9d01c4645bb  2016-07-05T06:02:00.000Z   
4  810bbb53-a095-4dd2-9661-2a10e1112e69  2016-07-05T11:50:00.000Z   

   policeAction  agentPresence relatedRecord        contextInfo transports  \
0          True           True          None      Ação policial         []   
1          True           True          None      Ação policial         []   
2         False          False          None   Não identificado         []   
3          True           True          None  Operação policial         []   
4          True           True          None  Operação policial         []   

                                             victims animalVictims  \
0                                                 []            []   
1                                                 []            []   
2                                                 []            []   
3  [{'id': 'b59f5be1-9df5-495a-8952-c67d60234af4'...            []   
4                                                 []            []   

                         geometry  
0  POINT (667875.995 7461282.402)  
1  POINT (677236.207 7470268.211)  
2   POINT (678136.361 7466354.26)  
3  POINT (634913.994 7464771.511)  
4  POINT (669896.222 7474841.328)

In [76]:
shots = (
    gpd
    .read_file('outputs/S300/fogo_cruzado.gpkg')
    .assign(
        date=lambda db: pd.to_datetime(db.date)
        )
    .pipe(
        lambda x: x.loc[x.date < '2020-01-01']
        )
    )
    

DataSourceError: outputs/S300/fogo_cruzado.gpkg: No such file or directory

### KDE

In [ ]:
model = KernelDensity(bandwidth=300, kernel='gaussian')
slice_shots = shots.pipe(
        lambda x: x.loc[x.date >= '2023-01-01']
        )
fit = model.fit(
  X=list(zip(slice_shots.geometry.x, slice_shots.geometry.y)),
  )
    

db = (
    h3fy(area, resolution=9)
    .to_crs(area.estimate_utm_crs(datum_name='SIRGAS2000'))
    .assign(**{
        'X': lambda df: df.centroid.x,
        'Y': lambda df: df.centroid.y
    })
)

db = (
    db
    .assign(**{
        f'gunshot_kde': lambda df: np.exp(
            fit.score_samples(
                X=df[['X', 'Y']].to_numpy()
                )
            )
        })    
    )


c:\Users\brand\anaconda3\envs\roda\Lib\site-packages\pyproj\crs\crs.py:1295: UserWarning: You will likely lose important projection information when converting to a PROJ string from another format. See: https://proj.org/faq.html#what-is-the-best-format-for-describing-coordinate-reference-systems
  proj = self._crs.to_proj4(version=version)


In [ ]:
db.explore('gunshot_kde', cmap='inferno', scheme='headtailbreaks', prefer_canvas=True)